# Partitioned Circuit Extraction Walkthrough

Final phase of the circuit partioning framework is the extraction of a partitioned quanutm circuit. 

Using the QuantumCircuitHyperGraph object and a node assignment function, we can infer the required teleportation operations and build a quantum cirucit.
The qubits are split across multiple registers - one for each partition. Each partition is also initialised with a communication qubit register and a classical bit register for facilitating the teleportation. Additional communication qubits may be added if there are not enough available.

## Build initial circuit

First build/import and transpile the circuit. We use a fixed depth random circuit as an example.

In [54]:
from disqco.circuits.cp_fraction import cp_fraction
from disqco.circuits.QAOA import QAOA_random
from disqco.graphs.GCP_hypergraph import QuantumCircuitHyperGraph
from qiskit import transpile
from disqco.parti.FM.FM_methods import set_initial_partitions
from qiskit.circuit.library import QFT, QuantumVolume, EfficientSU2
from disqco.utils.qiskit_to_op_list import *
from qiskit import QuantumCircuit
import numpy as np

num_qubits = 64

seed= np.random.randint(0,1000000)

circuit = cp_fraction(  num_qubits = num_qubits,
                        depth = 64,
                        fraction= 0.5,
                        seed=seed)

# circuit = QuantumVolume(num_qubits, 30, seed= seed)
# circuit = QAOA_random(num_qubits, prob=0.5, reps=1)

num_qubits = circuit.num_qubits

circuit = transpile(circuit, basis_gates=['u', 'cp'])
depth = circuit.depth()

print(seed)


250307


## Graph building

We then build the graph using the QuantumCircuitHyperGraph object. We also define the paremeteres of the QPU architecture using the qpu_info and comm_info variables, which tell us how many physical qubits are in each partition.

We can draw the resulting graph using matplotlib. 

In [55]:

num_partitions = 4
qpu_size = int(num_qubits / num_partitions) + 1
qpu_info = [qpu_size] * num_partitions

comm_info = [1] * num_partitions

group_gates = True

graph = QuantumCircuitHyperGraph(circuit = circuit,
                                 group_gates = group_gates,
                                 anti_diag = True)


from disqco.graphs.quantum_network import QuantumNetwork

qnet = QuantumNetwork(qpu_info)

assignment = set_initial_partitions(network = qnet, 
                                    num_qubits = num_qubits, 
                                    depth = depth)

from disqco.parti.FM.FM_methods import calculate_full_cost

cost = calculate_full_cost(graph, assignment, num_partitions)

print("E-bit cost for unoptimised assignment: ", cost)


Number of layers: 66
E-bit cost for unoptimised assignment:  579


In [56]:
from disqco.drawing.tikz_drawing import *
from disqco.drawing.mpl_drawing import *
%load_ext jupyter_tikz

if num_qubits <= 32:
    fig = draw_graph_tikz(H=graph,assignment=assignment,qpu_info=qpu_info)

    display(fig)


The jupyter_tikz extension is already loaded. To reload it, use:
  %reload_ext jupyter_tikz


## Naive extraction

We can first set a baseline for the distributed circuit by extracting a partitioned circuit directly from the unoptimised assignment function. This will likely result in a very deep circuit which does not use entanglement efficiently.

First import the extractor class, passing in the graph and the partition assignment that we initialised before.

In [57]:
from disqco.circuit_extraction.circuit_extractor_new import PartitionedCircuitExtractor



extractor = PartitionedCircuitExtractor(graph=graph, 
                                         partition_assignment=assignment, 
                                         qpu_info=qpu_info, 
                                         comm_info=comm_info)



basic_partitioned_circuit = extractor.extract_partitioned_circuit()

basic_partitioned_circuit_EPR = transpile(basic_partitioned_circuit, basis_gates=['cp','u','EPR'])

print(f"Depth of partitioned circuit: {basic_partitioned_circuit.depth()}")

EPR_count = basic_partitioned_circuit_EPR.count_ops()['EPR']
print(f"EPR count in partitioned circuit: {EPR_count}")



Processing layer 0
Processing group gate {'type': 'group', 'root': 32, 'time': 0, 'sub-gates': [{'type': 'two-qubit', 'name': 'cp', 'qargs': [32, 11], 'qregs': ['q', 'q'], 'params': [0.011306454788220508], 'time': 0}, {'type': 'two-qubit', 'name': 'cp', 'qargs': [32, 33], 'qregs': ['q', 'q'], 'params': [4.145754517768183], 'time': 1}]} at time 0
Logical to physical index mapping: {0: Qubit(QuantumRegister(17, 'Q0_q'), 0), 1: Qubit(QuantumRegister(17, 'Q0_q'), 1), 2: Qubit(QuantumRegister(17, 'Q0_q'), 2), 3: Qubit(QuantumRegister(17, 'Q0_q'), 3), 4: Qubit(QuantumRegister(17, 'Q0_q'), 4), 5: Qubit(QuantumRegister(17, 'Q0_q'), 5), 6: Qubit(QuantumRegister(17, 'Q0_q'), 6), 7: Qubit(QuantumRegister(17, 'Q0_q'), 7), 8: Qubit(QuantumRegister(17, 'Q0_q'), 8), 9: Qubit(QuantumRegister(17, 'Q0_q'), 9), 10: Qubit(QuantumRegister(17, 'Q0_q'), 10), 11: Qubit(QuantumRegister(17, 'Q0_q'), 11), 12: Qubit(QuantumRegister(17, 'Q0_q'), 12), 13: Qubit(QuantumRegister(17, 'Q0_q'), 13), 14: Qubit(QuantumReg

We can draw the circuit to see where the teleportation blocks are occurring.

In [58]:
if num_qubits < 12:
    fig = basic_partitioned_circuit.draw(output='mpl', style='bw', fold=100)
    fig.show()


To compare with original, we can transpile back into the U, CP gate-set, while choosing not to decompose the elementary entanglement generation options.

In [59]:
decomposed_circuit = transpile(basic_partitioned_circuit, basis_gates = ['cp', 'u', 'EPR'])

print(f"Depth of decomposed partitioned circuit: {decomposed_circuit.depth()}")

# decomposed_circuit.draw(output='mpl', style='bw', fold=50)

Depth of decomposed partitioned circuit: 2687


We now optimise the node assignments using the recursive multilevel partitioning FM algorithm.

In [60]:
from disqco.parti.FM.multilevel_FM import MLFM_recursive
import numpy as np
from disqco.parti.FM.FM_main import run_FM

assignment_list, cost_list, _ = MLFM_recursive(
    graph,
    assignment,
    qpu_info,
    limit = num_qubits,
    log = True)


final_cost = min(cost_list)
final_assignment = assignment_list[np.argmin(cost_list)]

# if num_qubits <= 32:    
#     fig = draw_graph_tikz(H=graph,assignment=final_assignment,qpu_info=qpu_info)
#     display(fig)

Number of layers: 66
Number of layers: 66
Number of layers: 66
Number of layers: 66
Number of layers: 66
Number of layers: 66
Initial cost: 579
All passes complete.
Final cost: 481
Best cost at level 0: 481
Initial cost: 481
All passes complete.
Final cost: 460
Best cost at level 1: 460
Initial cost: 460
All passes complete.
Final cost: 429
Best cost at level 2: 429
Initial cost: 429
All passes complete.
Final cost: 409
Best cost at level 3: 409
Initial cost: 409
All passes complete.
Final cost: 397
Best cost at level 4: 397
Initial cost: 397
All passes complete.
Final cost: 392
Best cost at level 5: 392
Initial cost: 392
All passes complete.
Final cost: 391
Best cost at level 6: 391


Now define a new extractor for with the optimised assignment. 

In [61]:


extractor_opt = PartitionedCircuitExtractor(graph = graph, 
                                            partition_assignment = final_assignment, 
                                            qpu_info = qpu_info, 
                                            comm_info=comm_info)

partitioned_circuit_opt = extractor_opt.extract_partitioned_circuit()


print(f"Depth of optimised partitioned circuit: {partitioned_circuit_opt.depth()}")

partitioned_circuit_opt_EPR = transpile(partitioned_circuit_opt, basis_gates = ['cp', 'u', 'EPR'])

if 'EPR' in partitioned_circuit_opt_EPR.count_ops():
    EPR_count_opt = partitioned_circuit_opt_EPR.count_ops()['EPR']
else:
    EPR_count_opt = 0

print(f"EPR count in optimised partitioned circuit: {EPR_count_opt}")




Processing layer 0
Processing group gate {'type': 'group', 'root': 32, 'time': 0, 'sub-gates': [{'type': 'two-qubit', 'name': 'cp', 'qargs': [32, 11], 'qregs': ['q', 'q'], 'params': [0.011306454788220508], 'time': 0}, {'type': 'two-qubit', 'name': 'cp', 'qargs': [32, 33], 'qregs': ['q', 'q'], 'params': [4.145754517768183], 'time': 1}]} at time 0
Logical to physical index mapping: {0: Qubit(QuantumRegister(17, 'Q2_q'), 0), 1: Qubit(QuantumRegister(17, 'Q3_q'), 0), 2: Qubit(QuantumRegister(17, 'Q0_q'), 0), 3: Qubit(QuantumRegister(17, 'Q3_q'), 1), 4: Qubit(QuantumRegister(17, 'Q0_q'), 1), 5: Qubit(QuantumRegister(17, 'Q1_q'), 0), 6: Qubit(QuantumRegister(17, 'Q3_q'), 2), 7: Qubit(QuantumRegister(17, 'Q0_q'), 2), 8: Qubit(QuantumRegister(17, 'Q2_q'), 1), 9: Qubit(QuantumRegister(17, 'Q0_q'), 3), 10: Qubit(QuantumRegister(17, 'Q0_q'), 4), 11: Qubit(QuantumRegister(17, 'Q0_q'), 5), 12: Qubit(QuantumRegister(17, 'Q2_q'), 2), 13: Qubit(QuantumRegister(17, 'Q2_q'), 3), 14: Qubit(QuantumRegiste

In [62]:
decomposed_circuit_opt = transpile(partitioned_circuit_opt, basis_gates = ['cp', 'u', 'EPR'])
print(f"Depth of decomposed partitioned circuit: {decomposed_circuit_opt.depth()}")

def get_wire_order(qc):
    """
    Build a valid wire_order from segments such as registers.
    Each segment must be an iterable of Bit objects.
    """


    reg_dict = {i : [] for i in range(num_partitions)}
    reg_list = []
    for reg in qc.qregs:
        QPU = int(reg.name[1])
        reg_dict[QPU].append(reg)
        
    for  i in range(num_partitions):
        for reg in reg_dict[i]:
            reg_list.append(reg)

    for creg in qc.cregs:
        reg_list.append(creg)
    
    bits = [bit for segment in reg_list for bit in segment]
    # if not creg_bundle:
    #     bits += qc.clbits  # show the remaining classical bits, if desired
    # if use_ints:
    idx = {b: i for i, b in enumerate(qc.qubits + qc.clbits)}
    return [idx[b] for b in bits]



# decomposed_circuit_opt.draw(output='mpl', style='bw', fold=50)



wo = get_wire_order(decomposed_circuit_opt)

print(wo)

# print(reg_dict)  
# # for creg in partitioned_circuit_opt.cregs:
# #     reg_dict[creg.name] = creg
# wire_order = []
# for i in range(num_partitions):
#     for reg in reg_dict[i]:
#         for qubit in reg:
#             print(qubit)
#             wire_order.append(qubit)

# print(wire_order)


partitioned_circuit_opt.draw(output='mpl', wire_order=wo, style='bw', fold=50)



Depth of decomposed partitioned circuit: 2480
[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 68, 72, 80, 100, 101, 102, 103, 105, 107, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 69, 76, 81, 83, 84, 92, 95, 96, 97, 98, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 70, 74, 75, 82, 85, 86, 87, 90, 91, 93, 94, 99, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 71, 73, 77, 78, 79, 88, 89, 104, 106, 108, 109, 110, 111, 112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 125, 126, 127, 128, 129, 130, 131, 132, 133, 134, 135, 136, 137, 138, 139, 140, 141, 142, 143, 144, 145, 146, 147, 148, 149, 150, 151, 152, 153, 154, 155, 156, 157, 158, 159, 160, 161, 162, 163, 164, 165, 166, 167, 168, 169, 170, 171, 172, 173]


KeyboardInterrupt: 

The depth of the resulting circuit should significantly lower than the unoptimised variant, though of course still much larger than the un-partitioned circuit. Some additional overhead is unavoidable.

## Validation

We would like to validate the output given by the partitioned circuit, which we can do using qiskits sampler class.

First we need to add measurements to the original, unpartitioned circuit.

In [24]:
from disqco.circuit_extraction.verification import run_sampler, plot, get_fidelity

circuit.measure_all()

data_circuit = run_sampler(circuit, shots=100000)
plot(data_circuit)



Too many qubits
No data to plot


In [25]:
# data_partitioned_circuit = run_sampler(basic_partitioned_circuit, shots=100000)
# plot(data_partitioned_circuit)


In [26]:
# data_partitioned_circuit_optimised = run_sampler(partitioned_circuit_opt, shots=100000)
# plot(data_partitioned_circuit_optimised)

In [27]:
# fidelity = get_fidelity(data_circuit, data_partitioned_circuit, shots=100000)

# print(f"Fidelity between original and unoptimised partitioned circuit: {fidelity}")

In [28]:
# fidelity = get_fidelity(data_circuit, data_partitioned_circuit_optimised, shots=100000)

# print(f"Fidelity between original and optimised partitioned circuit: {fidelity}")